# OBJEKTINIS PROGRAMAVIMAS

### Duomenų atsisiuntimas (Coingecko API):

ohlc (Open/High/Low/Close):

In [ ]:
import requests
from datetime import datetime
from dateutil import parser

base_url = "https://api.coingecko.com/api/v3/coins/bitcoin/ohlc"

params = {
    'vs_currency': 'usd',
    'days': '7',
}

headers = {
    "accept": "application/json",
    "x-cg-demo-api-key": ""
}

response = requests.get(base_url, params=params, headers=headers)
data = response.json()

def format_timestamp(timestamp):
    return datetime.utcfromtimestamp(timestamp/1000).strftime('%Y-%m-%d %H:%M:%S')

print("OHLC Data for the Last 2 Days:")
#print(data)
for entry in data:
    print(entry[0])
    time = format_timestamp(entry[0])
    open_price = entry[1]
    high_price = entry[2]
    low_price = entry[3]
    close_price = entry[4]
    print(f"Time: {time}, Open: {open_price}, High: {high_price}, Low: {low_price}, Close: {close_price}")

OHLC Data for the Last 2 Days:
1717444800000
Time: 2024-06-03 20:00:00, Open: 69763.0, High: 69763.0, Low: 68875.0, Close: 69069.0
1717459200000
Time: 2024-06-04 00:00:00, Open: 69098.0, High: 69470.0, Low: 68732.0, Close: 68808.0
1717473600000
Time: 2024-06-04 04:00:00, Open: 68810.0, High: 69343.0, Low: 68744.0, Close: 69150.0
1717488000000
Time: 2024-06-04 08:00:00, Open: 69149.0, High: 69237.0, Low: 68732.0, Close: 69058.0
1717502400000
Time: 2024-06-04 12:00:00, Open: 68972.0, High: 69074.0, Low: 68544.0, Close: 68920.0
1717516800000
Time: 2024-06-04 16:00:00, Open: 68961.0, High: 70569.0, Low: 68844.0, Close: 70569.0
1717531200000
Time: 2024-06-04 20:00:00, Open: 70413.0, High: 71018.0, Low: 70062.0, Close: 70263.0
1717545600000
Time: 2024-06-05 00:00:00, Open: 70425.0, High: 70711.0, Low: 70201.0, Close: 70600.0
1717560000000
Time: 2024-06-05 04:00:00, Open: 70542.0, High: 71235.0, Low: 70444.0, Close: 70868.0
1717574400000
Time: 2024-06-05 08:00:00, Open: 70995.0, High: 71313.0

### Norint gauti VOLUME turime naudoti kitą nuorodą:

In [ ]:
import requests
from datetime import datetime

base_url = "https://api.coingecko.com/api/v3/coins/bitcoin/market_chart"

params = {
    'vs_currency': 'usd',
    'days': '7'  # Get data for the last 7 days
}

headers = {
    "accept": "application/json",
    "x-cg-demo-api-key": "CG-HWFe76jzP5YcNf1qKdiSY4VL"
}

response = requests.get(base_url, params=params, headers=headers)
data = response.json()

def format_timestamp(timestamp):
    return datetime.utcfromtimestamp(timestamp / 1000).strftime('%Y-%m-%d %H:%M:%S')

prices = data['prices']
volumes = data['total_volumes']


print("OHLC and Volume Data for the Last 7 Days:")
for i in range(len(prices)):
    time = format_timestamp(prices[i][0])
    price = prices[i][1]
    volume = volumes[i][1]
    print(f"Time: {time}, Price: {price}, Volume: {volume}")

OHLC and Volume Data for the Last 7 Days:
Time: 2024-06-03 19:01:23, Price: 69222.414378, Volume: 30018278644.1606
Time: 2024-06-03 20:08:11, Price: 69290.18723123687, Volume: 29701192747.200317
Time: 2024-06-03 21:08:14, Price: 69123.47887328567, Volume: 29906664983.140537
Time: 2024-06-03 22:02:18, Price: 69013.04238036116, Volume: 30254954583.87357
Time: 2024-06-03 23:09:30, Price: 69005.28049701726, Volume: 30358753702.080475
Time: 2024-06-04 00:05:16, Price: 68809.78520249174, Volume: 25735381259.850346
Time: 2024-06-04 01:03:23, Price: 68993.03011420573, Volume: 30721958753.510273
Time: 2024-06-04 02:05:52, Price: 69187.85395378836, Volume: 29280880072.333164
Time: 2024-06-04 03:03:48, Price: 69097.86394215949, Volume: 28752894554.199627
Time: 2024-06-04 04:08:23, Price: 69068.12651217902, Volume: 29116866216.644135
Time: 2024-06-04 05:01:56, Price: 69041.25822711401, Volume: 28803440800.623695
Time: 2024-06-04 06:07:09, Price: 68864.94517712682, Volume: 28508162909.899426
Time: 

### Sujungiame abi užklausas bei išfiltruojame po vieną įrašą iš 2 paskutinių dienų:

In [ ]:
import requests
from datetime import datetime, timedelta

ohlc_url = "https://api.coingecko.com/api/v3/coins/bitcoin/ohlc"
market_chart_url = "https://api.coingecko.com/api/v3/coins/bitcoin/market_chart"
params = {
    'vs_currency': 'usd',
    'days': '7'
}
headers = {
    "accept": "application/json",
    "x-cg-demo-api-key": "CG-HWFe76jzP5YcNf1qKdiSY4VL"
}

def is_midnight(timestamp):
    dt = datetime.utcfromtimestamp(timestamp / 1000)
    return dt.hour == 0 and dt.minute == 0 and dt.second == 0

def format_timestamp(timestamp):
    return datetime.utcfromtimestamp(timestamp / 1000).strftime('%Y-%m-%d %H:%M:%S')

def find_closest_volume(timestamp, volume_data):
    closest_volume, closest_diff = None, 10e10
    for vol_entry in volume_data:
        vol_timestamp = vol_entry[0]
        diff = abs(timestamp - vol_timestamp)
        if diff < closest_diff:
            closest_diff = diff
            closest_volume = vol_entry[1]
            closest_timestamp = vol_timestamp
    return closest_volume

response_ohlc = requests.get(ohlc_url, params=params, headers=headers)
response_market_chart = requests.get(market_chart_url, params=params, headers=headers)

if response_ohlc.ok and response_market_chart.ok:
    ohlc_data = response_ohlc.json()
    market_data = response_market_chart.json()
    results = []
    today = datetime.utcnow()
    start_date = today - timedelta(days=2)
    for entry in ohlc_data:
        timestamp = entry[0]
        if is_midnight(timestamp) and datetime.utcfromtimestamp(timestamp / 1000) >= start_date:
            open_price, high_price, low_price, close_price = entry[1:]
            time_formatted = format_timestamp(timestamp)
            volume = find_closest_volume(timestamp, market_data['total_volumes'])
            results.append({
                'date': time_formatted,
                'open': open_price,
                'high': high_price,
                'low': low_price,
                'close': close_price,
                'volume': volume
            })
    for result in results:
        print(result)
else:
    if response_ohlc.status_code != 200: print(f'bitcoin/ohlc ERROR: {response_ohlc.text}')
    if response_market_chart.status_code != 200: print(f'bitcoin/market_chart ERROR: {response_market_chart.text}')


{'date': '2024-06-09 00:00:00', 'open': 69459.0, 'high': 69459.0, 'low': 69284.0, 'close': 69315.0, 'volume': 12847962289.456978}
{'date': '2024-06-10 00:00:00', 'open': 69714.0, 'high': 69795.0, 'low': 69561.0, 'close': 69654.0, 'volume': 12177078985.637917}


# Aplikacija su integruotu Coingecko API:

In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import Lasso
from sklearn.ensemble import RandomForestRegressor
import sqlite3
import warnings
import requests
from datetime import datetime, timedelta

class BTCModel:
    def __init__(self, data_path, reviews_path, random_forest=False, use_extended_features=False):
        self.btc_all = pd.read_csv(data_path)
        self.reviews = pd.read_csv(reviews_path, sep='|')
        self.scaler = StandardScaler()
        self.random_forest = random_forest
        self.use_extended_features = use_extended_features

        if random_forest:
            self.model = RandomForestRegressor(
                max_depth=None, min_samples_leaf=2, min_samples_split=2, n_estimators=300, random_state=73
            )
        else:
            self.model = Lasso(alpha=75, max_iter=25000, tol=0.001, random_state=0)

        self._preprocess()
        self._train()

    def _preprocess(self):
        self.reviews['Date'] = pd.to_datetime(self.reviews['Date'], errors='coerce')
        self.reviews = self.reviews.dropna(subset=['Date'])
        self.reviews['YearMonth'] = self.reviews['Date'].dt.to_period('M')
        monthly_mean_rating = self.reviews.groupby('YearMonth')['Rating'].mean().reset_index()
        monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()
        self.btc_all['Date'] = pd.to_datetime(self.btc_all['Date'])
        self.btc_all['YearMonth'] = self.btc_all['Date'].dt.to_period('M')
        btc_merged = pd.merge(self.btc_all, monthly_mean_rating, on='YearMonth', how='left')
        btc_merged['Date'] = btc_merged['Date_x']
        btc_merged = btc_merged.drop(columns=['Date_x', 'Date_y'])
        btc_merged['Rating'].fillna(method='ffill', inplace=True)
        btc_merged['Lag_Close_1'] = btc_merged['Close'].shift(1)
        btc_merged['Lag_Close_2'] = btc_merged['Close'].shift(2)
        btc_merged['Lag_Volume_1'] = btc_merged['Volume'].shift(1)
        btc_merged['Lag_Volume_2'] = btc_merged['Volume'].shift(2)
        btc_merged['Lag_Open_1'] = btc_merged['Open'].shift(1)
        btc_merged['Lag_Open_2'] = btc_merged['Open'].shift(2)
        btc_merged['Lag_High_1'] = btc_merged['High'].shift(1)
        btc_merged['Lag_High_2'] = btc_merged['High'].shift(2)
        btc_merged['Lag_Low_1'] = btc_merged['Low'].shift(1)
        btc_merged['Lag_Low_2'] = btc_merged['Low'].shift(2)
        btc_merged.dropna(inplace=True)
        btc_merged['Day'] = btc_merged['Date'].dt.day
        btc_merged['Month'] = btc_merged['Date'].dt.month
        btc_merged['Year'] = btc_merged['Date'].dt.year
        self.btc_all = btc_merged

    def _train(self):
        if self.use_extended_features:
            features = [
                'Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2',
                'Lag_Open_1', 'Lag_Open_2', 'Lag_High_1', 'Lag_High_2', 'Lag_Low_1', 'Lag_Low_2',
                'Day', 'Month', 'Year', 'Rating'
            ]
        else:
            features = [
                'Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2',
                'Day', 'Month', 'Year', 'Rating'
            ]

        X = self.btc_all[features]
        y = self.btc_all['Close']

        assert len(X) == len(y), "Feature X and target y arrays length mismatch!"

        X_train = X.copy()
        y_train = y.copy()

        assert len(X_train) == len(y_train), "Training feature X_train and target arrays y_train length mismatch!"

        X_train = self.scaler.fit_transform(X_train)
        self.model.fit(X_train, y_train)

    def _fetch_coingecko_data(self):
        ohlc_url = "https://api.coingecko.com/api/v3/coins/bitcoin/ohlc"
        market_chart_url = "https://api.coingecko.com/api/v3/coins/bitcoin/market_chart"
        params = {
            'vs_currency': 'usd',
            'days': '7'
        }
        headers = {
            "accept": "application/json",
            "x-cg-demo-api-key": "CG-HWFe76jzP5YcNf1qKdiSY4VL"
        }

        response_ohlc = requests.get(ohlc_url, params=params, headers=headers)
        response_market_chart = requests.get(market_chart_url, params=params, headers=headers)

        if response_ohlc.ok and response_market_chart.ok:
            ohlc_data = response_ohlc.json()
            market_data = response_market_chart.json()
            results = []
            today = datetime.utcnow()
            start_date = today - timedelta(days=2)
            for entry in ohlc_data:
                timestamp = entry[0]
                if self._is_midnight(timestamp) and datetime.utcfromtimestamp(timestamp / 1000) >= start_date:
                    open_price, high_price, low_price, close_price = entry[1:]
                    time_formatted = self._format_timestamp(timestamp)
                    volume = self._find_closest_volume(timestamp, market_data['total_volumes'])
                    results.append({
                        'date': time_formatted,
                        'open': open_price,
                        'high': high_price,
                        'low': low_price,
                        'close': close_price,
                        'volume': volume
                    })
            for result in results:
                print(result)
            return results
        else:
            if response_ohlc.status_code != 200:
                print(f'bitcoin/ohlc ERROR: {response_ohlc.text}')
            if response_market_chart.status_code != 200:
                print(f'bitcoin/market_chart ERROR: {response_market_chart.text}')
            raise ValueError("API ERROR.")

    def _get_lag_data_from_api(self):
        btc_data = self._fetch_coingecko_data()
        date_plus_one = datetime.now() + timedelta(days=1)
        data = {
            'Lag_Close_1': btc_data[1]['close'],
            'Lag_Close_2': btc_data[0]['close'],
            'Lag_Volume_1': btc_data[1]['volume'],
            'Lag_Volume_2': btc_data[0]['volume'],
            'Lag_Open_1': btc_data[1]['open'],
            'Lag_Open_2': btc_data[0]['open'],
            'Lag_High_1': btc_data[1]['high'],
            'Lag_High_2': btc_data[0]['high'],
            'Lag_Low_1': btc_data[1]['low'],
            'Lag_Low_2': btc_data[0]['low'],
            'Day': date_plus_one.day,
            'Month': date_plus_one.month,
            'Year': date_plus_one.year,
            'Rating': 1.4
        }
        return data

    def predict(self, user_input=None, date=None, use_api=False):
        warnings.filterwarnings("ignore", message="X does not have valid feature names, but StandardScaler was fitted with feature names")
        if use_api:
            user_input_processed = self._get_lag_data_from_api()
            user_input_scaled = self.scaler.transform([list(user_input_processed.values())])
        elif user_input is not None and date is None:
            user_input_processed = self._preprocess_user_input(user_input)
            user_input_scaled = self.scaler.transform([user_input_processed])
        elif date is not None:
            user_input = self._get_lag_data(date)
            user_input_scaled = self.scaler.transform([list(user_input.values())])
        else:
            raise ValueError("ERROR.")

        prediction = self.model.predict(user_input_scaled)
        return prediction[0]

    def _preprocess_user_input(self, user_input):
        if self.use_extended_features:
            return [
                user_input['Lag_Close_1'],
                user_input['Lag_Close_2'],
                user_input['Lag_Volume_1'],
                user_input['Lag_Volume_2'],
                user_input['Lag_Open_1'],
                user_input['Lag_Open_2'],
                user_input['Lag_High_1'],
                user_input['Lag_High_2'],
                user_input['Lag_Low_1'],
                user_input['Lag_Low_2'],
                user_input['Day'],
                user_input['Month'],
                user_input['Year'],
                user_input['Rating']
            ]
        else:
            return [
                user_input['Lag_Close_1'],
                user_input['Lag_Close_2'],
                user_input['Lag_Volume_1'],
                user_input['Lag_Volume_2'],
                user_input['Day'],
                user_input['Month'],
                user_input['Year'],
                user_input['Rating']
            ]

    def _get_lag_data(self, date):
        date = pd.to_datetime(date)
        if date > self.btc_all['Date'].max():
            most_recent = self.btc_all.iloc[-1]
            if self.use_extended_features:
                return {
                    'Lag_Close_1': most_recent['Close'],
                    'Lag_Close_2': most_recent['Lag_Close_1'],
                    'Lag_Volume_1': most_recent['Volume'],
                    'Lag_Volume_2': most_recent['Lag_Volume_1'],
                    'Lag_Open_1': most_recent['Open'],
                    'Lag_Open_2': most_recent['Lag_Open_1'],
                    'Lag_High_1': most_recent['High'],
                    'Lag_High_2': most_recent['Lag_High_1'],
                    'Lag_Low_1': most_recent['Low'],
                    'Lag_Low_2': most_recent['Lag_Low_1'],
                    'Day': date.day,
                    'Month': date.month,
                    'Year': date.year,
                    'Rating': most_recent['Rating']
                }
            else:
                return {
                    'Lag_Close_1': most_recent['Close'],
                    'Lag_Close_2': most_recent['Lag_Close_1'],
                    'Lag_Volume_1': most_recent['Volume'],
                    'Lag_Volume_2': most_recent['Lag_Volume_1'],
                    'Day': date.day,
                    'Month': date.month,
                    'Year': date.year,
                    'Rating': most_recent['Rating']
                }
        row = self.btc_all[self.btc_all['Date'] == date]
        if row.empty:
            row = self.btc_all[self.btc_all['Date'] < date].iloc[-1]
        if self.use_extended_features:
            return {
                'Lag_Close_1': row['Lag_Close_1'].values[0],
                'Lag_Close_2': row['Lag_Close_2'].values[0],
                'Lag_Volume_1': row['Lag_Volume_1'].values[0],
                'Lag_Volume_2': row['Lag_Volume_2'].values[0],
                'Lag_Open_1': row['Lag_Open_1'].values[0],
                'Lag_Open_2': row['Lag_Open_2'].values[0],
                'Lag_High_1': row['Lag_High_1'].values[0],
                'Lag_High_2': row['Lag_High_2'].values[0],
                'Lag_Low_1': row['Lag_Low_1'].values[0],
                'Lag_Low_2': row['Lag_Low_2'].values[0],
                'Day': date.day,
                'Month': date.month,
                'Year': date.year,
                'Rating': row['Rating'].values[0]
            }
        else:
            return {
                'Lag_Close_1': row['Lag_Close_1'].values[0],
                'Lag_Close_2': row['Lag_Close_2'].values[0],
                'Lag_Volume_1': row['Lag_Volume_1'].values[0],
                'Lag_Volume_2': row['Lag_Volume_2'].values[0],
                'Day': date.day,
                'Month': date.month,
                'Year': date.year,
                'Rating': row['Rating'].values[0]
            }

    def _is_midnight(self, timestamp):
        dt = datetime.utcfromtimestamp(timestamp / 1000)
        return dt.hour == 0 and dt.minute == 0 and dt.second == 0

    def _format_timestamp(self, timestamp):
        return datetime.utcfromtimestamp(timestamp / 1000).strftime('%Y-%m-%d %H:%M:%S')

    def _find_closest_volume(self, timestamp, volume_data):
        closest_volume, closest_diff = None, 10e10
        for vol_entry in volume_data:
            vol_timestamp = vol_entry[0]
            diff = abs(timestamp - vol_timestamp)
            if diff < closest_diff:
                closest_diff = diff
                closest_volume = vol_entry[1]
        return closest_volume

class user_inputDatabase:
    def __init__(self, db_path):
        self.db_path = db_path
        self._initialize_db()

    def _initialize_db(self):
        conn = sqlite3.connect(self.db_path)
        c = conn.cursor()
        c.execute('''CREATE TABLE IF NOT EXISTS user_inputs
                     (Lag_Close_1 REAL, Lag_Close_2 REAL, Lag_Volume_1 REAL, Lag_Volume_2 REAL,
                      Lag_Open_1 REAL, Lag_Open_2 REAL, Lag_High_1 REAL, Lag_High_2 REAL, Lag_Low_1 REAL, Lag_Low_2 REAL,
                      Day INTEGER, Month INTEGER, Year INTEGER, Rating REAL)''')
        conn.commit()
        conn.close()

    def save_user_input(self, user_input):
        conn = sqlite3.connect(self.db_path)
        c = conn.cursor()
        columns = ', '.join(user_input.keys())
        placeholders = ', '.join('?' * len(user_input))
        values = tuple(user_input.values())

        query = f"INSERT INTO user_inputs ({columns}) VALUES ({placeholders})"
        c.execute(query, values)

        conn.commit()
        conn.close()


In [ ]:
import json
from datetime import datetime

try_again = 'Neteisinga įvestis, bandykite dar kartą.'

def get_float_input(prompt, quit_char='q'):
    while True:
        inp = input(prompt).strip().lower()
        if inp == quit_char:
            return quit_char
        try:
            return float(inp)
        except ValueError:
            print(try_again)

def get_int_input(prompt, quit_char='q'):
    while True:
        inp = input(prompt).strip().lower()
        if inp == quit_char:
            return quit_char
        try:
            return int(inp)
        except ValueError:
            print(try_again)

def get_date_input(prompt, format="%Y-%m-%d", quit_char='q'):
    while True:
        inp = input(prompt).strip().lower()
        if inp == quit_char:
            return quit_char
        try:
            return datetime.strptime(inp, format)
        except ValueError:
            print(try_again)

def main():
    db_path = 'inputs_btc2_advanced.db'
    user_db = user_inputDatabase(db_path)
    print("BTC Prediction Model")
    date = None
    model = None
    data_path = 'combined_btc2_data.csv'
    reviews_path = 'trustpilot_coinbase_reviews-strip.csv'
    user_input = {}

    print("Norėdami įšeiti įveskite 'q'")

    use_api = input("Ar norite naudoti API? (y/n)").strip().lower()
    if use_api == 'q':
        return

    if use_api == 'y':
        print("Parsisiunčiami duomenys...")
        model = BTCModel(data_path, reviews_path, random_forest=False, use_extended_features=True)
        #user_input = model._get_lag_data_from_api()
    else:
        extended_features = input("Ar norite naudoti visus įvesties duomenis? (y/n)\nNenaudojant visos įvesties spėjimams bus naudojama tik data.").strip().lower()
        if extended_features == 'q':
            return
        if extended_features == 'y':
            print("Įveskite paskutinių 2 dienų duomenis:")
            user_input['Lag_Close_1'] = get_float_input("Lag_Close_1: ")
            user_input['Lag_Close_2'] = get_float_input("Lag_Close_2: ")
            user_input['Lag_Volume_1'] = get_float_input("Lag_Volume_1: ")
            user_input['Lag_Volume_2'] = get_float_input("Lag_Volume_2: ")
            user_input['Lag_Open_1'] = get_float_input("Lag_Open_1: ")
            user_input['Lag_Open_2'] = get_float_input("Lag_Open_2: ")
            user_input['Lag_High_1'] = get_float_input("Lag_High_1: ")
            user_input['Lag_High_2'] = get_float_input("Lag_High_2: ")
            user_input['Lag_Low_1'] = get_float_input("Lag_Low_1: ")
            user_input['Lag_Low_2'] = get_float_input("Lag_Low_2: ")
            user_input['Day'] = get_int_input("Nuspėjama diena: ")
            user_input['Month'] = get_int_input("Mėnuo: ")
            user_input['Year'] = get_int_input("Metai: ")
            user_input['Rating'] = get_float_input("Vidutinis einamojo mėn. Coinbase reitingas: ")
        else:
            date = get_date_input("Įveskite datą BTC kainos nuspėjimui (YYYY-MM-DD): ")
            if date == 'q':
                return
            user_input['Day'] = date.day
            user_input['Month'] = date.month
            user_input['Year'] = date.year

    if 'Rating' not in user_input or user_input['Rating'] is None:
        user_input['Rating'] = 1.4

    default_keys = ['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2',
                    'Lag_Open_1', 'Lag_Open_2', 'Lag_High_1', 'Lag_High_2',
                    'Lag_Low_1', 'Lag_Low_2', 'Day', 'Month', 'Year', 'Rating']

    for key in default_keys:
         user_input.setdefault(key, 0.0 if 'L' in key else 0)

    if not model:
        model = BTCModel(data_path, reviews_path, random_forest=False, use_extended_features=extended_features)

    if date:
        prediction = model.predict(date=date, use_api=use_api == 'y')
    else:
        prediction = model.predict(user_input=user_input, use_api=use_api == 'y')

    if use_api == 'y':
        print(f"Nuspėjama modelio su API BTC kaina rytdienai --> {prediction:,.2f} USD <--")
    else:
        print(f"Nuspėjama modelio BTC kaina šiam laikotarpiui ({user_input['Year']}-{user_input['Month']}-{user_input['Day']}) --> {prediction:,.2f} USD <--")

    user_db.save_user_input(user_input)

if __name__ == "__main__":
    main()


BTC Prediction Model
Norėdami įšeiti įveskite 'q'
Nuspėjama modelio BTC kaina šiam laikotarpiui (2024-9-1) --> 69,031.21 USD <--
